In [0]:
import pandas as pd
dbutils.fs.cp("dbfs:/FileStore/tables/Online_Retail.csv", "file:/tmp/Online_Retail.csv")
df = pd.read_csv("/tmp/Online_Retail.csv")

df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype  
---  ------       --------------   -----  
 0   InvoiceNo    541909 non-null  object 
 1   StockCode    541909 non-null  object 
 2   Description  540455 non-null  object 
 3   Quantity     541909 non-null  int64  
 4   InvoiceDate  541909 non-null  object 
 5   UnitPrice    541909 non-null  float64
 6   CustomerID   406829 non-null  float64
 7   Country      541909 non-null  object 
dtypes: float64(2), int64(1), object(5)
memory usage: 33.1+ MB


In [0]:
df.head()

InvoiceNo 
 StockCode 
 Description 
 Quantity 
 InvoiceDate 
 UnitPrice 
 CustomerID 
 Country 
 
 
 
 
 0 
 536365 
 85123A 
 WHITE HANGING HEART T-LIGHT HOLDER 
 6 
 01-12-2010 08:26 
 2.55 
 17850.0 
 United Kingdom 
 
 
 1 
 536365 
 71053 
 WHITE METAL LANTERN 
 6 
 01-12-2010 08:26 
 3.39 
 17850.0 
 United Kingdom 
 
 
 2 
 536365 
 84406B 
 CREAM CUPID HEARTS COAT HANGER 
 8 
 01-12-2010 08:26 
 2.75 
 17850.0 
 United Kingdom 
 
 
 3 
 536365 
 84029G 
 KNITTED UNION FLAG HOT WATER BOTTLE 
 6 
 01-12-2010 08:26 
 3.39 
 17850.0 
 United Kingdom 
 
 
 4 
 536365 
 84029E 
 RED WOOLLY HOTTIE WHITE HEART. 
 6 
 01-12-2010 08:26 
 3.39 
 17850.0 
 United Kingdom

In [0]:
df.isnull().sum()

Out[3]: InvoiceNo           0
StockCode           0
Description      1454
Quantity            0
InvoiceDate         0
UnitPrice           0
CustomerID     135080
Country             0
dtype: int64

In [0]:
#drop rows with missing cutomer id
df = df.dropna(subset=['CustomerID'])

#removing cancelled transactions( invoices starting with 'C')
df=df[~df['InvoiceNo'].astype(str).str.startswith('C')]

#keeping only positive quantity values
df = df[df['Quantity']>0]

#convert invoicedate to datetime format
df['InvoiceDate']=pd.to_datetime(df['InvoiceDate'])

#creating a new column totalprice for the monetary value of transactions.
df['TotalPrice']=df['Quantity']*df['UnitPrice']

In [0]:
df.head()

InvoiceNo 
 StockCode 
 Description 
 Quantity 
 InvoiceDate 
 UnitPrice 
 CustomerID 
 Country 
 TotalPrice 
 
 
 
 
 0 
 536365 
 85123A 
 WHITE HANGING HEART T-LIGHT HOLDER 
 6 
 2010-01-12 08:26:00 
 2.55 
 17850.0 
 United Kingdom 
 15.30 
 
 
 1 
 536365 
 71053 
 WHITE METAL LANTERN 
 6 
 2010-01-12 08:26:00 
 3.39 
 17850.0 
 United Kingdom 
 20.34 
 
 
 2 
 536365 
 84406B 
 CREAM CUPID HEARTS COAT HANGER 
 8 
 2010-01-12 08:26:00 
 2.75 
 17850.0 
 United Kingdom 
 22.00 
 
 
 3 
 536365 
 84029G 
 KNITTED UNION FLAG HOT WATER BOTTLE 
 6 
 2010-01-12 08:26:00 
 3.39 
 17850.0 
 United Kingdom 
 20.34 
 
 
 4 
 536365 
 84029E 
 RED WOOLLY HOTTIE WHITE HEART. 
 6 
 2010-01-12 08:26:00 
 3.39 
 17850.0 
 United Kingdom 
 20.34

In [0]:
#convert the pandas df to a spark df
spark_df = spark.createDataFrame(df)

In [0]:
#registering the spark df as a temp SQL view
spark_df.createOrReplaceTempView("online_retail_cleaned")

In [0]:
%sql
SELECT * FROM online_retail_cleaned

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country TotalPrice 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 2010-01-12T08:26:00.000+0000 2.55 17850.0 United Kingdom 15.299999999999999 536365 71053 WHITE METAL LANTERN 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 2010-01-12T08:26:00.000+0000 2.75 17850.0 United Kingdom 22.0 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 2010-01-12T08:26:00.000+0000 7.65 17850.0 United Kingdom 15.3 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 2010-01-12T08:26:00.000+0000 4.25 17850.0 United Kingdom 25.5 536366 22633 HAND WARMER UNION JACK 6 2010-01-12T08:28:00.000+0000 1.85 17850.0 United Kingdom 11.100000000000001 536366 22632 HAND WARMER RED POLKA DOT 6 2010-01-12T08:28:00.000+0000 1.85 17850.0 United Kingdom 11.100000000000001 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 2010-01-12T08:34:00.000+0000 1.69 13047.0 United Kingdom 54.08 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 2010-01-12T08:34:00.000+0000 2.1 13047.0 United Kingdom 12.600000000000001 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 2010-01-12T08:34:00.000+0000 2.1 13047.0 United Kingdom 12.600000000000001 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 2010-01-12T08:34:00.000+0000 3.75 13047.0 United Kingdom 30.0 536367 22310 IVORY KNITTED MUG COSY 6 2010-01-12T08:34:00.000+0000 1.65 13047.0 United Kingdom 9.899999999999999 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 2010-01-12T08:34:00.000+0000 4.25 13047.0 United Kingdom 25.5 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 2010-01-12T08:34:00.000+0000 9.95 13047.0 United Kingdom 19.9 536367 21754 HOME BUILDING BLOCK WORD 3 2010-01-12T08:34:00.000+0000 5.95 13047.0 United Kingdom 17.85 536367 21755 LOVE BUILDING BLOCK WORD 3 2010-01-12T08:34:00.000+0000 5.95 13047.0 United Kingdom 17.85 536367 21777 RECIPE BOX WITH METAL HEART 4 2010-01-12T08:34:00.000+0000 7.95 13047.0 United Kingdom 31.8 536367 48187 DOORMAT NEW ENGLAND 4 2010-01-12T08:34:00.000+0000 7.95 13047.0 United Kingdom 31.8 536368 22960 JAM MAKING SET WITH JARS 6 2010-01-12T08:34:00.000+0000 4.25 13047.0 United Kingdom 25.5 536368 22913 RED COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536368 22912 YELLOW COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536368 22914 BLUE COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536369 21756 BATH BUILDING BLOCK WORD 3 2010-01-12T08:35:00.000+0000 5.95 13047.0 United Kingdom 17.85 536370 22728 ALARM CLOCK BAKELIKE PINK 24 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 90.0 536370 22727 ALARM CLOCK BAKELIKE RED 24 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 90.0 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 45.0 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 2010-01-12T08:45:00.000+0000 0.85 12583.0 France 10.2 536370 21883 STARS GIFT TAPE 24 2010-01-12T08:45:00.000+0000 0.65 12583.0 France 15.600000000000001 536370 10002 INFLATABLE POLITICAL GLOBE 48 2010-01-12T08:45:00.000+0000 0.85 12583.0 France 40.8 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 2010-01-12T08:45:00.000+0000 1.25 12583.0 France 30.0 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 2010-01-12T08:45:00.000+0000 2.95 12583.0 France 53.1 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 2010-01-12T08:45:00.000+0000 2.95 12583.0 France 70.80000000000001 536370 22629 SPACEBOY LUNCH BOX 24 2010-01-12T08:45:00.000+0000 1.95 12583.0 France 46.8 536370 22659 LUNCH BOX

In [0]:
%sql
-- total revenue generated
SELECT round(sum(TotalPrice),2) AS Total_Revenue
FROM online_retail_cleaned;


Total_Revenue 8911407.9

In [0]:
%sql
--top 10 best selling products by quantity
SELECT Description, SUM(Quantity) AS Total_Units_Sold
FROM online_retail_cleaned
GROUP BY Description
ORDER BY Total_Units_Sold DESC
LIMIT 10;

Description Total_Units_Sold PAPER CRAFT , LITTLE BIRDIE 80995 MEDIUM CERAMIC TOP STORAGE JAR 77916 WORLD WAR 2 GLIDERS ASSTD DESIGNS 54415 JUMBO BAG RED RETROSPOT 46181 WHITE HANGING HEART T-LIGHT HOLDER 36725 ASSORTED COLOUR BIRD ORNAMENT 35362 PACK OF 72 RETROSPOT CAKE CASES 33693 POPCORN HOLDER 30931 RABBIT NIGHT LIGHT 27202 MINI PAINT SET VINTAGE 26076

In [0]:
%sql
SELECT date_format(InvoiceDate,'yyyy-MM') AS Month, round(sum(TotalPrice),2) AS Monthly_Revenue
FROM online_retail_cleaned
GROUP BY Month
ORDER BY Month;

Month Monthly_Revenue 2010-01 46376.49 2010-02 47316.53 2010-03 23921.71 2010-05 31771.6 2010-06 31215.64 2010-07 53795.31 2010-08 39248.82 2010-09 38231.9 2010-10 33650.28 2010-12 227185.61 2011-01 601804.6 2011-02 487100.63 2011-03 646325.52 2011-04 602872.24 2011-05 719269.56 2011-06 688561.56 2011-07 735451.04 2011-08 608723.7 2011-09 1095156.87 2011-10 904826.42 2011-11 1043411.07 2011-12 205190.8

In [0]:
%sql
--revenue by country(excluding UK)
SELECT Country , round(sum(TotalPrice),2) AS Revenue
FROM online_retail_cleaned 
WHERE Country != 'United Kingdom'
GROUP BY Country
ORDER BY Revenue DESC;

Country Revenue Netherlands 285446.34 EIRE 265545.9 Germany 228867.14 France 209024.05 Australia 138521.31 Spain 61577.11 Switzerland 56443.95 Belgium 41196.34 Sweden 38378.33 Japan 37416.37 Norway 36165.44 Portugal 33439.89 Finland 22546.08 Singapore 21279.29 Channel Islands 20450.44 Denmark 18955.34 Italy 17483.24 Cyprus 13590.38 Austria 10198.68 Poland 7334.65 Israel 7221.69 Greece 4760.52 Iceland 4310.0 Canada 3666.38 USA 3580.39 Malta 2725.59 Unspecified 2667.07 United Arab Emirates 1902.28 Lebanon 1693.88 Lithuania 1661.06 European Community 1300.25 Brazil 1143.6 RSA 1002.31 Czech Republic 826.74 Bahrain 548.4 Saudi Arabia 145.92

In [0]:
%sql
-- top 10 spending customers
SELECT CustomerID, round(sum(TotalPrice),2) as Total_Spent
FROM online_retail_cleaned
GROUP BY CustomerID
ORDER BY Total_Spent DESC
LIMIT 10;

CustomerID Total_Spent 14646.0 280206.02 18102.0 259657.3 17450.0 194550.79 16446.0 168472.5 14911.0 143825.06 12415.0 124914.53 14156.0 117379.63 17511.0 91062.38 16029.0 81024.84 12346.0 77183.6

In [0]:
%sql
-- average order value 
SELECT ROUND(sum(TotalPrice)/Count(DISTINCT InvoiceNo),2) as Average_Order_Value
FROM online_retail_cleaned;

Average_Order_Value 480.76

In [0]:
display(df)

InvoiceNo StockCode Description Quantity InvoiceDate UnitPrice CustomerID Country TotalPrice 536365 85123A WHITE HANGING HEART T-LIGHT HOLDER 6 2010-01-12T08:26:00.000+0000 2.55 17850.0 United Kingdom 15.299999999999999 536365 71053 WHITE METAL LANTERN 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 84406B CREAM CUPID HEARTS COAT HANGER 8 2010-01-12T08:26:00.000+0000 2.75 17850.0 United Kingdom 22.0 536365 84029G KNITTED UNION FLAG HOT WATER BOTTLE 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 84029E RED WOOLLY HOTTIE WHITE HEART. 6 2010-01-12T08:26:00.000+0000 3.39 17850.0 United Kingdom 20.34 536365 22752 SET 7 BABUSHKA NESTING BOXES 2 2010-01-12T08:26:00.000+0000 7.65 17850.0 United Kingdom 15.3 536365 21730 GLASS STAR FROSTED T-LIGHT HOLDER 6 2010-01-12T08:26:00.000+0000 4.25 17850.0 United Kingdom 25.5 536366 22633 HAND WARMER UNION JACK 6 2010-01-12T08:28:00.000+0000 1.85 17850.0 United Kingdom 11.100000000000001 536366 22632 HAND WARMER RED POLKA DOT 6 2010-01-12T08:28:00.000+0000 1.85 17850.0 United Kingdom 11.100000000000001 536367 84879 ASSORTED COLOUR BIRD ORNAMENT 32 2010-01-12T08:34:00.000+0000 1.69 13047.0 United Kingdom 54.08 536367 22745 POPPY'S PLAYHOUSE BEDROOM 6 2010-01-12T08:34:00.000+0000 2.1 13047.0 United Kingdom 12.600000000000001 536367 22748 POPPY'S PLAYHOUSE KITCHEN 6 2010-01-12T08:34:00.000+0000 2.1 13047.0 United Kingdom 12.600000000000001 536367 22749 FELTCRAFT PRINCESS CHARLOTTE DOLL 8 2010-01-12T08:34:00.000+0000 3.75 13047.0 United Kingdom 30.0 536367 22310 IVORY KNITTED MUG COSY 6 2010-01-12T08:34:00.000+0000 1.65 13047.0 United Kingdom 9.899999999999999 536367 84969 BOX OF 6 ASSORTED COLOUR TEASPOONS 6 2010-01-12T08:34:00.000+0000 4.25 13047.0 United Kingdom 25.5 536367 22623 BOX OF VINTAGE JIGSAW BLOCKS 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536367 22622 BOX OF VINTAGE ALPHABET BLOCKS 2 2010-01-12T08:34:00.000+0000 9.95 13047.0 United Kingdom 19.9 536367 21754 HOME BUILDING BLOCK WORD 3 2010-01-12T08:34:00.000+0000 5.95 13047.0 United Kingdom 17.85 536367 21755 LOVE BUILDING BLOCK WORD 3 2010-01-12T08:34:00.000+0000 5.95 13047.0 United Kingdom 17.85 536367 21777 RECIPE BOX WITH METAL HEART 4 2010-01-12T08:34:00.000+0000 7.95 13047.0 United Kingdom 31.8 536367 48187 DOORMAT NEW ENGLAND 4 2010-01-12T08:34:00.000+0000 7.95 13047.0 United Kingdom 31.8 536368 22960 JAM MAKING SET WITH JARS 6 2010-01-12T08:34:00.000+0000 4.25 13047.0 United Kingdom 25.5 536368 22913 RED COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536368 22912 YELLOW COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536368 22914 BLUE COAT RACK PARIS FASHION 3 2010-01-12T08:34:00.000+0000 4.95 13047.0 United Kingdom 14.850000000000001 536369 21756 BATH BUILDING BLOCK WORD 3 2010-01-12T08:35:00.000+0000 5.95 13047.0 United Kingdom 17.85 536370 22728 ALARM CLOCK BAKELIKE PINK 24 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 90.0 536370 22727 ALARM CLOCK BAKELIKE RED 24 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 90.0 536370 22726 ALARM CLOCK BAKELIKE GREEN 12 2010-01-12T08:45:00.000+0000 3.75 12583.0 France 45.0 536370 21724 PANDA AND BUNNIES STICKER SHEET 12 2010-01-12T08:45:00.000+0000 0.85 12583.0 France 10.2 536370 21883 STARS GIFT TAPE 24 2010-01-12T08:45:00.000+0000 0.65 12583.0 France 15.600000000000001 536370 10002 INFLATABLE POLITICAL GLOBE 48 2010-01-12T08:45:00.000+0000 0.85 12583.0 France 40.8 536370 21791 VINTAGE HEADS AND TAILS CARD GAME 24 2010-01-12T08:45:00.000+0000 1.25 12583.0 France 30.0 536370 21035 SET/2 RED RETROSPOT TEA TOWELS 18 2010-01-12T08:45:00.000+0000 2.95 12583.0 France 53.1 536370 22326 ROUND SNACK BOXES SET OF4 WOODLAND 24 2010-01-12T08:45:00.000+0000 2.95 12583.0 France 70.80000000000001 536370 22629 SPACEBOY LUNCH BOX 24 2010-01-12T08:45:00.000+0000 1.95 12583.0 France 46.8 536370 22659 LUNCH BOX